In [1]:
from ngsolve import *
from netgen.csg import *
from netgen.meshing import MeshingStep
from ngsolve.webgui import Draw

import numpy as np

In [4]:
def exact_solution(x, y, z, t):
    #return np.sin(x) * np.sin(y) * np.sin(z) * t
    return sin(z) * t

In [47]:
convergence_results = []

# Time-stepping parameters
n_runs = 3
T = 1  # Total simulation time
num_steps = 10 # Initial number of time steps


vertex0_solution = np.zeros((n_runs,))  # Solution at convergence_vertex_id for each run

convergence_vertex_id = 0
convergence_point = mesh.vertices[convergence_vertex_id].point
convergence_results = []

final_run = False

for run in range(n_runs):
    
    geo = CSGeometry()
    geo.Add(Sphere(Pnt(0,0,0),1))
    mesh = Mesh(geo.GenerateMesh(maxh=0.4/(run + 1), perfstepsend=MeshingStep.MESHSURFACE))
    mesh.Curve(2)
    
    print("Run: ", run)
    if (run == (n_runs - 1)):
        print("Final run!")
        final_run = True
        
    print("Position: ", mesh.vertices[convergence_vertex_id].point)
    
    #evaluation_point = mesh(0,0,1)
    
    
    #V = H1(mesh, order=1, dirichlet_bbnd="bottom")
    V = H1(mesh, order=1)
    u,v = V.TnT()
    gfu_last = GridFunction(V)
    gfu_last.Set(0, definedon=mesh.Boundaries(".*"))
    gfu = GridFunction(V)
    gfu.Set(0)
    gfu.Set(0, definedon=mesh.Boundaries(".*"))
    
    
    myt = Parameter(0.0)
    rhs_function = sin(z)+myt*sin(z) \
        + 2*(myt*z*cos(z))/(sqrt(x**2 + y**2 + z**2)) \
        - (myt*z**2*sin(z))/(x**2 + y**2 + z**2)
    myf = LinearForm(V)
    myf += rhs_function*v*ds
    
    
    gfunc = GridFunction(V)
    gfsolution = GridFunction(V)
    num_vertices = mesh.nv
    
    dt = T / num_steps
    print("Number of steps: ", num_steps)
    print("Number of vertices: ", num_vertices)
    
    
    a = BilinearForm(V, symmetric=True)
    a += grad(u).Trace()*grad(v).Trace()*ds
    a.Assemble()

    m = BilinearForm(V, symmetric=True)
    m += u*v*ds
    m.Assemble()
    
    # Assemble the system matrix
    system_matrix = m.mat.CreateMatrix()
    print(f"Mmatrix.mat.nze = {m.mat.nze}, Amatrix.mat.nze={a.mat.nze}, system_matrix.nze={system_matrix.nze}")
    
    system_matrix.AsVector().data = m.mat.AsVector() + dt * a.mat.AsVector()
    inv_system_matrix = system_matrix.Inverse(freedofs=V.FreeDofs())
    
    # Time-stepping loop
    for step in range(num_steps):
        
        time = dt * (step+1)
        print("Time: ", time)
        myt.Set(time)
        myf.Assemble()
        
        #rhs_vector = Mmatrix.mat*gfu_last.vec + dt*f.vec
        #gfu.vec.data = inv_system_matrix*rhs_vector
        ## Update the solution for the next iteration
        #gfu_last.vec.data = gfu.vec.data
        
        ## Incremental form
        rhs_vector = dt*myf.vec - dt * a.mat * gfu.vec
        gfu.vec.data += inv_system_matrix * rhs_vector


        # Output for visualization (replace this with your actual visualization)
        if (final_run == True):
            gfunc.vec.data = gfu.vec.data
            gfsolution.AddMultiDimComponent(gfu.vec)
        
    
    vertex0_solution[run] = gfu.vec[convergence_vertex_id]


    if (final_run == True):
        print("Final solution")
        # Show the final solution
        Draw(gfunc, "Final Solution")
    else:
        num_steps *= 2
        mesh.Refine() # doesnt work for surface meshes
        print("Mesh refined!")

Run:  0
Position:  (0.12345, 0.54321, 0.8304715488203073)
Number of steps:  10
Number of vertices:  98
Mmatrix.mat.nze = 674, Amatrix.mat.nze=674, system_matrix.nze=674
Time:  0.1
Time:  0.2
Time:  0.30000000000000004
Time:  0.4
Time:  0.5
Time:  0.6000000000000001
Time:  0.7000000000000001
Time:  0.8
Time:  0.9
Time:  1.0
Mesh refined!
Run:  1
Position:  (0.12345, 0.54321, 0.8304715488203073)
Number of steps:  20
Number of vertices:  331
Mmatrix.mat.nze = 2305, Amatrix.mat.nze=2305, system_matrix.nze=2305
Time:  0.05
Time:  0.1
Time:  0.15000000000000002
Time:  0.2
Time:  0.25
Time:  0.30000000000000004
Time:  0.35000000000000003
Time:  0.4
Time:  0.45
Time:  0.5
Time:  0.55
Time:  0.6000000000000001
Time:  0.65
Time:  0.7000000000000001
Time:  0.75
Time:  0.8
Time:  0.8500000000000001
Time:  0.9
Time:  0.9500000000000001
Time:  1.0
Mesh refined!
Run:  2
Final run!
Position:  (0.12345, 0.54321, 0.8304715488203073)
Number of steps:  40
Number of vertices:  755
Mmatrix.mat.nze = 5273, A

WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.2…

In [48]:
vertex0_solution

array([0.7502368 , 0.74165752, 0.73976817])

In [49]:
exact_solution(convergence_point[0], convergence_point[1], convergence_point[2], T)

0.7382495259241072

In [50]:
vertex0_error = np.abs(vertex0_solution - exact_solution(convergence_point[0], convergence_point[1], convergence_point[2], T))

convergence_rates = []

# Compute convergence rates for each pair of consecutive errors
for i in range(len(vertex0_error) - 1):
    rate = np.log(vertex0_error[i] / vertex0_error[i+1]) / np.log(2)
    convergence_rates.append(rate)

convergence_rates

[1.8145105864771185, 1.1661422218235036]

In [27]:
convergence_point

(0.12345, 0.54321, 0.8304715488203073)

In [ ]:
time = 1
exact_last_solution1 = sin(z)*time
# Create a FESpace and a GridFunction for the function
gflast = GridFunction(V)
gflast.Set(exact_last_solution1,  definedon=mesh.Boundaries(".*"))
Draw(gflast)